In [13]:
import os
import re
import xml.etree.ElementTree as ET

xml_files = [f for f in os.listdir('../../data/raw_data') if f.endswith('.xml')]

results = []

for i in range(len(xml_files)):  
    file_path = os.path.join('../../data/raw_data', xml_files[i]) 
    tree = ET.parse(file_path)  
    root = tree.getroot()  
    
    data = {}

    data["id"] = re.sub(r'\D', '', xml_files[i])

    # 출원 번호
    elem1 = root.find('.//biblioSummaryInfo')
    title = elem1.findtext('inventionTitle', '') if elem1 is not None else ''
    
    # 요약
    elem2 = root.find('.//abstractInfoArray/abstractInfo')
    abstract = elem2.findtext('astrtCont', '')  if elem2 is not None else ''

    # 청구항
    claims = {}

    for elem in root.findall('.//claimInfoArray/claimInfo/claim'):
        full = elem.text.strip()            
        num = full.split('.')[0]          
        value = full.split('.', 1)[1].strip()
        claims[f"claim{num}"] = value

    for claim_key in claims:
        claim_text = claims[claim_key]
        
        independent = not bool(re.search(r"(?:제\s*\d+\s*항|청구항\s*\d+)\s*에\s*있어서,?", claim_text))

        claim_text = re.sub(r"(?:제\s*\d+\s*항|청구항\s*\d+)\s*에\s*있어서,?", "", claim_text).strip()
        
        claims[claim_key] = {
            "content": claim_text,
            "independent": independent
        }

    data["embed"] = {'name':title, 'abstract':abstract, 'claim':claims}

    # IPC
    ipc = []

    for elem in root.findall('.//ipcInfoArray/ipcInfo/ipcNumber'):
        text = elem.text or ''
        ipc.append(text if text else '')

    # 우선권(국가)
    elem5 = root.find('.//priorityInfoArray/priorityInfo')
    country = elem5.findtext('priorityApplicationCountry', '') if elem5 is not None else ''

    # 공개/거절
    status = elem1.findtext('registerStatus', '') if elem1 is not None else ''

    # 링크
    elem6 = root.find('.//imagePathInfo')
    link = elem6.findtext('largePath', '') if elem6 is not None else ''

    data["metadata"] = {'ipc':ipc, 'priority':country, 'register':status, 'link':link}

    results.append(data)

In [14]:
results

[{'id': '1020050108060',
  'embed': {'name': '정보 교류 기능을 가진 단말기, 이를 이용한 정보 교류시스템 및 방법',
   'abstract': ' 본 발명에 따른 단말기는 근거리 무선 통신을 통해 주변의 타 단말기 또는 서버와 정보를 교류할 수 있다. 또한 단말기 또는 서버는 자체에 데이터베이스를 구비하고 있어 타 단말기를 상대로 서비스 항목 정보를 교류 또는 GPS와 연계된 식별정보 등을 송수신할 수 있다. 본 발명의 특징적인 양상은 이 같은 단말기들이 주변의 타 단말기들의 식별정보, 위치정보와 같은 상황 정보를 직접 또는 서버로부터 수집하여 매 시각별로 저장함으로써 주변의 타 단말기 소지자들과 정보를 교류하거나 특정한 시각의 당시 주위 단말기 배치 상황을 조회할 수 있도록 할 수도 있다.단말기, 미팅, 리서치, 고유정보, 서비스 항목 정보, 전자 상거래, 식별정보, GPS, 지도, 상황도, GIS',
   'claim': {'claim1': {'content': '주변의 다른 적어도 하나의 단말기와 통신하며 정보를 교류하는 단말기로서,상기 다른 단말기와의 통신 기능을 수행하는 통신부;단말기의 식별정보를 포함한 정보를 저장하는 메모리;상기 통신부를 통해 상기 다른 단말기에 원하는 정보를 요청하고, 요청된 정보를 수신하여 해당 서비스를 수행하는 제어부를 포함하는 단말기.',
     'independent': True},
    'claim2': {'content': 'GPS 위성의 신호를 수신하여 위치 계산에 필요한 정보를 출력하는 GPS 모듈을 더 포함하며, 상기 제어부는 상기 다른 단말기들의 위치 정보를 입력받고, 입력받은 다른 단말기의 위치와 자신의 위치로부터 상황도 정보를 생성하는 것을 특징으로 하는 단말기.',
     'independent': False},
    'claim3': {'content': '상기 제어부는,수신된 다른 단말기의 식별정보를 포함한 정보를 저장하는 주변 단말기 등록부와;외부로부터의 

In [15]:
# json 확장자로 저장
import json

with open('preprocessed_data_independent.jsonl', 'w', encoding='utf-8') as f:
    for data in results:  
        f.write(json.dumps(data, ensure_ascii=False) + '\n')
